<a href="https://colab.research.google.com/github/PaulaDCV/PropagandaDetection/blob/main/Propaganda.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Imports and setup

In [ ]:
import pandas as pd
import altair as alt
import numpy as np
import string
import re
import itertools as it
from collections import Counter


#Wandb
!pip install wandb
import wandb
wandb.login()
from wandb.sklearn import plot_precision_recall, plot_feature_importances
from wandb.sklearn import plot_class_proportions, plot_learning_curve, plot_roc

#Sklearn imports
import sklearn
from sklearn.dummy import DummyClassifier
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.naive_bayes import GaussianNB
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score
from sklearn.metrics import classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split

#Nltk imports
!pip install nltk
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
stopwords = stopwords.words('english')

#Transformers
!pip install -q transformers
!pip install -q datasets
!pip install evaluate

from transformers import pipeline
from datasets import Dataset
from transformers import AutoTokenizer
from transformers import AutoModelForSequenceClassification
from transformers import TrainingArguments, Trainer
import evaluate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


wandb: Currently logged in as: pauladelcastillovivero (pdc). Use `wandb login --relogin` to force relogin


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
#Mount google drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
#Read the data and connvert into a dataframe
train_path = "/content/drive/MyDrive/ANLP/propaganda_train.tsv"
test_path = "/content/drive/MyDrive/ANLP/propaganda_val.tsv"

traindf = pd.read_csv(train_path,sep='\t')
testdf = pd.read_table(test_path)

In [ ]:
#Add a column with a binary label 1-propaganda, 0-not propaganda
traindf["binary_label"] = np.where(traindf["label"] != "not_propaganda", 1,0)
testdf["binary_label"] = np.where(testdf["label"] != "not_propaganda", 1,0)

#Add a column removing the tags <BOS> and <EOS>
traindf["sentence"]=traindf["tagged_in_context"].str.replace('<BOS>', '')
traindf["sentence"]=traindf["sentence"].str.replace('<EOS>', '')
testdf["sentence"]=testdf["tagged_in_context"].str.replace('<BOS> ', '')
testdf["sentence"]=testdf["sentence"].str.replace('<EOS>', '')

#Extract span of text between BOS and EOS
traindf["span"] = traindf["tagged_in_context"].apply(lambda x: re.findall(r'<BOS> (.+?) <EOS>',str(x)))
traindf["span"] = traindf["span"].str[0]
traindf["span_length"] = traindf['span'].str.split().str.len()

#Calculate number of words in each span of text
testdf["span"] = testdf["tagged_in_context"].apply(lambda x: re.findall(r'<BOS> (.+?) <EOS>',str(x)))
testdf["span"] = testdf["span"].str[0]
testdf["span_length"] = testdf['span'].str.split().str.len()

#Length of sentence string
traindf["len"]=traindf["sentence"].str.len()
testdf["len"]=testdf["sentence"].str.len()

#Calculate number of words in each sentence
count = traindf['sentence'].str.split().apply(len).value_counts()
traindf["sentence_length"]=traindf['sentence'].str.split().str.len()
testdf["sentence_length"]=testdf['sentence'].str.split().str.len()

#DataFrame with all data
traindf["type"] = "Train"
testdf["type"] = "Test"
datadf = pd.concat([traindf,testdf])
datadf['binary_label'] = datadf['binary_label'].map({1: "Propaganda", 0:"Not Propaganda"})


In [ ]:
#Dataframe with just the propaganda senteneces for multiclass classification
propaganda_train_df = traindf[traindf["binary_label"]==1]
propaganda_test_df = testdf[testdf["binary_label"]==1]
propaganda_df = datadf[datadf["binary_label"]=="Propaganda"]

In [ ]:
datadf.to_csv("data.csv")

# EDA

### Class proportions

Training

In [ ]:
#Binary class proportions
percentage_train = traindf.groupby("binary_label").count().reset_index()
percentage_train["percentage"] = (percentage_train["tagged_in_context"] / percentage_train['tagged_in_context'].sum()) * 100
percentage_train

binary_label  label  tagged_in_context  sentence  span  span_length   len  \
0             0   1268               1268      1268  1268         1268  1268   
1             1   1290               1290      1290  1290         1290  1290   

   sentence_length  type  percentage  
0             1268  1268   49.569977  
1             1290  1290   50.430023

In [ ]:
#Binary class proportions
percentage_train = traindf.groupby("label").count().reset_index()
percentage_train["percentage"] = (percentage_train["tagged_in_context"] / percentage_train['tagged_in_context'].sum()) * 100
percentage_train

label  tagged_in_context  binary_label  sentence  span  \
0   appeal_to_fear_prejudice                157           157       157   157   
1  causal_oversimplification                165           165       165   165   
2                      doubt                157           157       157   157   
3  exaggeration,minimisation                169           169       169   169   
4                flag_waving                155           155       155   155   
5            loaded_language                161           161       161   161   
6      name_calling,labeling                166           166       166   166   
7             not_propaganda               1268          1268      1268  1268   
8                 repetition                160           160       160   160   

   span_length   len  sentence_length  type  percentage  
0          157   157              157   157    6.137608  
1          165   165              165   165    6.450352  
2          157   157              157   157    6.137608  
3          169   169              169   169    6.606724  
4          155   155              155   155    6.059421  
5          161   161              161   161    6.293980  
6          166   166              166   166    6.489445  
7         1268  1268             1268  1268   49.569977  
8          160   160              160   160    6.254887

In [ ]:
#Propaanada types class proportions
percentage_train = propaganda_train_df.groupby("label").count().reset_index()
percentage_train["percentage"] = (percentage_train["tagged_in_context"] / percentage_train['tagged_in_context'].sum()) * 100
percentage_train[["label","percentage"]]

label  percentage
0   appeal_to_fear_prejudice   12.170543
1  causal_oversimplification   12.790698
2                      doubt   12.170543
3  exaggeration,minimisation   13.100775
4                flag_waving   12.015504
5            loaded_language   12.480620
6      name_calling,labeling   12.868217
7                 repetition   12.403101

Testing

In [ ]:
percentage_test = testdf.groupby("label").count().reset_index()
percentage_test["percentage"] = (percentage_test["tagged_in_context"] / percentage_test['tagged_in_context'].sum()) * 100
percentage_test

label  tagged_in_context  binary_label  sentence  span  \
0   appeal_to_fear_prejudice                 43            43        43    43   
1  causal_oversimplification                 35            35        35    35   
2                      doubt                 43            43        43    43   
3  exaggeration,minimisation                 30            30        30    30   
4                flag_waving                 45            45        45    45   
5            loaded_language                 39            39        39    39   
6      name_calling,labeling                 34            34        34    34   
7             not_propaganda                331           331       331   331   
8                 repetition                 40            40        40    40   

   span_length  len  sentence_length  type  percentage  
0           43   43               43    43     6.71875  
1           35   35               35    35     5.46875  
2           43   43               43    43     6.71875  
3           30   30               30    30     4.68750  
4           45   45               45    45     7.03125  
5           39   39               39    39     6.09375  
6           34   34               34    34     5.31250  
7          331  331              331   331    51.71875  
8           40   40               40    40     6.25000

In [ ]:
percentage_test = testdf.groupby("binary_label").count().reset_index()
percentage_test["percentage"] = (percentage_test["tagged_in_context"] / percentage_test['tagged_in_context'].sum()) * 100
percentage_test

binary_label  label  tagged_in_context  sentence  span  span_length  len  \
0             0    331                331       331   331          331  331   
1             1    309                309       309   309          309  309   

   sentence_length  type  percentage  
0              331   331    51.71875  
1              309   309    48.28125

In [ ]:
#Propanada types class proportions
percentage_test = propaganda_test_df.groupby("label").count().reset_index()
percentage_test["percentage"] = (percentage_test["tagged_in_context"] / percentage_test['tagged_in_context'].sum()) * 100
percentage_test[["label","percentage"]]

label  percentage
0   appeal_to_fear_prejudice   13.915858
1  causal_oversimplification   11.326861
2                      doubt   13.915858
3  exaggeration,minimisation    9.708738
4                flag_waving   14.563107
5            loaded_language   12.621359
6      name_calling,labeling   11.003236
7                 repetition   12.944984

Graphs representing proportions

In [ ]:
data_per = datadf
data_per= data_per.groupby(["type", "label", "binary_label"]).size().reset_index(name="count")
data_per['binary_label'] = data_per['binary_label'].map({1: "Propaganda", 0:"Not Propaganda"})

test = data_per[data_per["type"]=="test"]
train = data_per[data_per["type"]=="train"]


test["percent"] = (test['count'] / test['count'].sum()) * 100
train["percent"] = (train['count'] / train['count'].sum()) * 100

data_per = pd.concat([test,train])
data_per


data =  alt.Chart(data_per, title = "     Class proportions", width={"step": 40}).mark_bar().encode(
    x=alt.X("binary_label:N", title = "Binary label"),
    y = alt.Y("percent", title = "Percentage(%)"),
    column = alt.Column("type", title="Dataset type"),
    color = alt.Color("label", title = "Label")
)
data

<ipython-input-102-d00679365f9c>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  test["percent"] = (test['count'] / test['count'].sum()) * 100
<ipython-input-102-d00679365f9c>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  train["percent"] = (train['count'] / train['count'].sum()) * 100


alt.Chart(...)

### Train split

In [ ]:
split = pd.DataFrame({"Type":["Test","Train","Train"],
              "Subtype":["Test","Train","Validation"],
              "Percentage":[0.2,0.6,0.2]})

In [ ]:
source = pd.DataFrame({"category": [1, 2, 3, 4, 5, 6], "value": [4, 6, 10, 3, 7, 8]})

alt.Chart(split).mark_arc().encode(
    theta="Percentage",
    color="Subtype"
)




alt.Chart(...)

### Length of sentences

#### Barchart

Average words in a sentence.

In [ ]:
#class
train_lendf = traindf.groupby("label").mean().reset_index()
test_lendf = testdf.groupby("label").mean().reset_index()

train = alt.Chart(train_lendf).mark_bar().encode(
    x = alt.X("label",title = "Label"),
    y = alt.Y("sentence_length", title = "Average sentence length")
)

test =  alt.Chart(test_lendf).mark_bar().encode(
    x = alt.X("label",title = "Label"),
    y = alt.Y("sentence_length", title = "Average sentence length")
)
train |test

alt.HConcatChart(...)

In [ ]:
#binary class
train_len_binary_df = traindf.groupby("binary_label").mean().reset_index()
test_len_binary_df = testdf.groupby("binary_label").mean().reset_index()

train = alt.Chart(train_len_binary_df, title ="Training data ").mark_bar().encode(
    x = alt.X("binary_label:N",title = "Label"),
    y = alt.Y("sentence_length", title = "Average character length")

)

test =  alt.Chart(test_len_binary_df, title ="Testing data ").mark_bar().encode(
    x = alt.X("binary_label:N",title = "Label"),
    y = alt.Y("sentence_length", title = "Average character length")
)
train | test

alt.HConcatChart(...)

Average words in each span, this is every word in between the \<BOS> and \<EOS> tag

In [ ]:
#class
train = alt.Chart(train_lendf, title ="Training data" ).mark_bar().encode(
    x = alt.X("label",title = "Label"),
    y = alt.Y("span_length", title = "Average span length")
)

test =  alt.Chart(test_lendf, title ="Testing data ").mark_bar().encode(
    x = alt.X("label",title = "Label"),
    y = alt.Y("span_length", title = "Average span length")
)
train |test

alt.HConcatChart(...)

In [ ]:
#binary class
train = alt.Chart(train_len_binary_df, title ="Training data ").mark_bar().encode(
    x = alt.X("binary_label:N",title = "Label"),
    y = alt.Y("sentence_length", title = "Average character length")

)

test =  alt.Chart(test_len_binary_df, title ="Testing data ").mark_bar().encode(
    x = alt.X("binary_label:N",title = "Label"),
    y = alt.Y("sentence_length", title = "Average words in a span")
)
train | test

alt.HConcatChart(...)

#### Boxplot

In [ ]:
#Length of sentence per class
alt.Chart(datadf).mark_boxplot(ticks = True, size = 10).encode(
    x= alt.X('type:O', axis = None,sort = ["Train, Test"]),
    y=alt.Y('sentence_length:Q', title = "Numnber of words",),
    color = "type:N",
    column = alt.Column("binary_label:N",align = "none",title = "Sentence length per class", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.1,
).configure_header(
    labelOrient = "bottom",
    labelAlign = "right",
    labelAngle = -75,
)

In [ ]:
#Length of span
alt.Chart(propaganda_df).mark_boxplot(ticks = True, size = 10).encode(
    x= alt.X('type:O', axis = None),
    y=alt.Y('span_length:Q', title = "Numnber of words"),
    color = "type:N",
    column = alt.Column("label:N",align = "none",title = "Span length class", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.1,
).configure_header(
    labelOrient = "bottom",
    labelAlign = "right",
    labelAngle = -75,
)

alt.Chart(...)

# Task 1 - binary

## Baseline

In [ ]:
from sklearn.dummy import DummyClassifier

corpus_train = traindf["sentence"]
labels_train = traindf["binary_label"].values

corpus_test = testdf["sentence"]
labels_test = testdf["binary_label"].values

# Create a dummy classifier that predicts classes randomly
random_clf = DummyClassifier(strategy='uniform', random_state=42)

# Train the classifier on your training data
random_clf.fit(corpus_train, labels_train)

# Test the classifier on your test data
labels_pred = random_clf.predict(corpus_test)
print(sklearn.metrics.classification_report(labels_test, labels_pred))


              precision    recall  f1-score   support

           0       0.52      0.48      0.50       331
           1       0.49      0.52      0.50       309

    accuracy                           0.50       640
   macro avg       0.50      0.50      0.50       640
weighted avg       0.50      0.50      0.50       640



## Random Forest

#### Data

In [ ]:
corpus_train = [s.translate(str.maketrans('', '', string.punctuation)) for s in traindf["sentence"].apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
corpus_train = [s.translate(str.maketrans("”"," ","")) for s in corpus_train]
corpus_train= [s.translate(str.maketrans("“"," ","")) for s in corpus_train]
labels_train = traindf["binary_label"].values

corpus_test = [s.translate(str.maketrans('', '', string.punctuation)) for s in testdf["sentence"].apply(lambda x: x.lower()).apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
corpus_test = [s.translate(str.maketrans("”"," ","")) for s in corpus_test]
corpus_test = [s.translate(str.maketrans("“"," ","")) for s in corpus_test]
labels_test = testdf["binary_label"].values

#### Sweep

In [ ]:
def run_sweep(name, max_depth, n_estimators, n_gram_range,max_features):
  vectorizer = CountVectorizer(analyzer = "word", ngram_range=n_gram_range)
  x_train = vectorizer.fit_transform(corpus_train)
  x_test = vectorizer.transform(corpus_test)
  feature_names = ["sentence"]
  labels = ["propaganda","not_propaganda"]
  test_size = 0.19372077488309952

  # train model
  model = RandomForestClassifier(n_estimators = n_estimators,
                                 max_features=max_features,
                                 max_depth =max_depth)
  model.fit(x_train, labels_train)
  model_params = model.get_params()
  model_params["n_gram_range"]=n_gram_range[1]
  # get predictions
  labels_pred = model.predict(x_test)
  labels_probas = model.predict_proba(x_test)
  importances = model.feature_importances_
  indices = np.argsort(importances)[::-1]

  # start a new wandb run and add your model hyperparameters
  wandb.init(project='NLP_RF1_', config=model_params, name = name)

  # Add additional configs to wandb
  wandb.config.update({"test_size" : test_size,
                      "train_len" : len(corpus_train),
                      "test_len" : len(corpus_test)})

  # log additional visualisations to wandb
  plot_class_proportions(labels_train, labels_test, labels)
  plot_learning_curve(model, x_train, labels_train)
  plot_roc(labels_test, labels_probas, labels)
  plot_precision_recall(labels_test, labels_probas, labels)
  plot_feature_importances(model)
  wandb.sklearn.plot_classifier(model, x_train, x_test,labels_train, labels_test, labels_pred, labels_probas, labels,
                                                         model_name=name, feature_names=None)

  #log metrics to wandb
  accuracy = sklearn.metrics.accuracy_score(labels_test, labels_pred)
  precision = sklearn.metrics.precision_score(labels_test, labels_pred)
  recall = sklearn.metrics.recall_score(labels_test, labels_pred)
  f1 = sklearn.metrics.f1_score(labels_test, labels_pred)

  wandb.summary["accuracy"] = accuracy
  wandb.summary["f1"] = f1
  wandb.summary["precision"] = precision
  wandb.summary["recall"] = recall

  # [optional] finish the wandb run, necessary in notebooks
  wandb.finish()

In [ ]:
param_grid = {
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [4,5,6,7,8],
}

param_combinations = sorted(param_grid)
param_combinations = [item for item in it.product(*(param_grid[param] for param in param_grid))]


Run multiple parameter combinations

In [ ]:
#Unigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(
            name = "unigram"+str(x),
            n_estimators = param[0],
            n_gram_range = (1,1),
            max_features = param[1],
            max_depth = param[2])
  n+=1

In [ ]:
#Bigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(
            name = "unigram"+str(x),
            n_estimators = param[0],
            n_gram_range = (1,1),
            max_features = param[1],
            max_depth = param[2])
  n+=1

In [ ]:
#Trigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(
            name = "unigram"+str(x),
            n_estimators = param[0],
            n_gram_range = (1,1),
            max_features = param[1],
            max_depth = param[2])
  n+=1

#### Final model

In [ ]:
vectorizer = CountVectorizer(analyzer = "word", ngram_range=(1,2))
x_train = vectorizer.fit_transform(corpus_train)
x_test = vectorizer.transform(corpus_test)
feature_names = ["sentence"]
labels = ["propaganda","not_propaganda"]
test_size = 0.19372077488309952

# train model
model = RandomForestClassifier(random_state = 21,
                               n_estimators = 6,
                               max_features="sqrt",
                               max_depth =200)
model.fit(x_train, labels_train)
model_params = model.get_params()
model_params["n_gram_range"]=2

# get predictions
labels_pred = model.predict(x_test)
labels_probas = model.predict_proba(x_test)
importances = model.feature_importances_
indices = np.argsort(importances)[::-1]
# start a new wandb run and add your model hyperparameters
wandb.init(project='NLP_RF1_', config=model_params, name = "Final")
# Add additional configs to wandb
wandb.config.update({"test_size" : test_size,
                    "train_len" : len(corpus_train),
                    "test_len" : len(corpus_test)})

# log additional visualisations to wandb
plot_class_proportions(labels_train, labels_test, labels)
plot_learning_curve(model, x_train, labels_train)
plot_roc(labels_test, labels_probas, labels)
plot_precision_recall(labels_test, labels_probas, labels)
plot_feature_importances(model)
wandb.sklearn.plot_classifier(model, x_train, x_test,labels_train, labels_test, labels_pred, labels_probas, labels,
                                                        model_name="Final", feature_names=None)
print(sklearn.metrics.classification_report(labels_test, labels_pred))

#log metrics to wandb
accuracy = sklearn.metrics.accuracy_score(labels_test, labels_pred)
precision = sklearn.metrics.precision_score(labels_test, labels_pred)
recall = sklearn.metrics.recall_score(labels_test, labels_pred)
f1 = sklearn.metrics.f1_score(labels_test, labels_pred)

wandb.summary["accuracy"] = accuracy
wandb.summary["f1"] = f1
wandb.summary["precision"] = precision
wandb.summary["recall"] = recall

# [optional] finish the wandb run, necessary in notebooks
wandb.finish()

wandb: Currently logged in as: pauladelcastillovivero (pdc). Use `wandb login --relogin` to force relogin


wandb: WARNING wandb.plots.* functions are deprecated and will be removed in a future release. Please use wandb.plot.* instead.
wandb: 
wandb: Plotting Final.
wandb: Logged feature importances.
wandb: Logged confusion matrix.
wandb: Logged summary metrics.
wandb: Logged class proportions.
wandb: Logged calibration curve.
wandb: Logged roc curve.
wandb: Logged precision-recall curve.


              precision    recall  f1-score   support

           0       0.62      0.80      0.70       331
           1       0.69      0.48      0.57       309

    accuracy                           0.65       640
   macro avg       0.66      0.64      0.63       640
weighted avg       0.66      0.65      0.64       640



In [ ]:
# get predictions
labels_pred_train = model.predict(x_train)
print(sklearn.metrics.classification_report(labels_train, labels_pred_train))


              precision    recall  f1-score   support

           0       0.84      0.97      0.90      1268
           1       0.97      0.81      0.88      1290

    accuracy                           0.89      2558
   macro avg       0.90      0.89      0.89      2558
weighted avg       0.90      0.89      0.89      2558



#### Results

In [ ]:
labels_pred = model.predict(x_test)
#Predictions to
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results.csv")
results_df["prob_prop_RF1"] = labels_probas[:,1]
results_df["predictions_RF1"]=labels_pred
results_df["accuracy_RF1"] = np.where(results_df["binary_label"] != results_df["predictions_RF1"], 0,1)

wrong_predictions = testdf[testdf["accuracy_RF1"] ==0]
wrong_predictions["sentence_"] = [s.translate(str.maketrans('', '', string.punctuation)) for s in wrong_predictions["sentence"].apply(lambda x: x.lower()).apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
wrong_predictions["sentence_"] =  [s.translate(str.maketrans("”"," ","")) for s in wrong_predictions["sentence_"]]
wrong_predictions["sentence_"] = [s.translate(str.maketrans("“"," ","")) for s in wrong_predictions["sentence_"] ]

#predicted as not propaganda when propaganda
wrong_predictions_as_not_propaganda = wrong_predictions[wrong_predictions["binary_label"] ==1]

#predicted as propaganda when not propaganda
wrong_predictions_as_propaganda = wrong_predictions[wrong_predictions["binary_label"] ==0 ]

<ipython-input-169-18ff57b78911>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  wrong_predictions["sentence_"] = [s.translate(str.maketrans('', '', string.punctuation)) for s in wrong_predictions["sentence"].apply(lambda x: x.lower()).apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
<ipython-input-169-18ff57b78911>:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  wrong_predictions["sentence_"] =  [s.translate(str.maketrans("”"," ","")) for s in wrong_predictions["senten

In [ ]:
results_df.to_csv("/content/drive/MyDrive/ANLP/results.csv", index = 0)

In [ ]:
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results.csv")

##### Graphs classes

In [ ]:
prop_answers = results_df.groupby(["predictions_RF1","accuracy_RF1"])["tagged_in_context"].count()
prop_answers = prop_answers.reset_index(name = "Count")
prop_answers["accuracy_RF1"] = prop_answers["accuracy_RF1"].map({1:"Correct",0:"Incorrect"})
prop_answers["predictions_RF1"] = prop_answers["predictions_RF1"].map({1:"Propaganda",0:"Not Propaganda"})

alt.Chart(prop_answers,
    title="Predictions per Class"
    ).mark_bar().encode(
    alt.Y("predictions_RF1:O",
          title = "Prediction"
          ),
    alt.X("Count",
          title="Percentage of answers(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color =alt.Color("accuracy_RF1:O", title = ""))

alt.Chart(...)

In [ ]:
right_answers =results_df.groupby(["binary_label","accuracy_RF1"])["tagged_in_context"].count()
right_answers = right_answers.reset_index(name ="count")
right_answers["accuracy_RF1"] = right_answers["accuracy_RF1"].map({1:"Correct",0:"Incorrect"})
right_answers["binary_label"] = right_answers["binary_label"].map({1:"Propaganda",0:"Not Propaganda"})

alt.Chart(right_answers,
    title= "Label"
    ).mark_bar().encode(
    y = alt.Y("binary_label:O",
          title = "True label"
          ),
    x = alt.X("count",
          title="Percentage of answers(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color = alt.Color("accuracy_RF1:O", title = "")
 )


alt.Chart(...)

In [ ]:
alt.Chart(
    wrong_predictions_as_not_propaganda,
    title= "Propaganda sentences labelled as Not propaganda"
    ).transform_joinaggregate(
    totalCount="count(*)"
    ).transform_calculate(
    PercentOfTotal="1 / datum.totalCount"
    ).mark_bar().encode(
    alt.Y("label",
          title = "True Label"),
    alt.X( "sum(PercentOfTotal):Q",
          title="Percentage of wrong answers(%)",
          axis=alt.Axis(format="%"),
          ),
    color =alt.Color("label", legend = None))

alt.Chart(...)

##### Frequency of words

In [ ]:
#get the words that appeared most in wrongly predicted sentences
top_words_wrong_predictions = Counter(" ".join(wrong_predictions["sentence_"]).split()).most_common(7)
top_words_wrong_predictions


Most frequent words in sentences predicted as not propaganda when propaganda

In [ ]:
top_words_wrong_predictions_as_not_propaganda = Counter(" ".join(wrong_predictions_as_not_propaganda["sentence_"]).split()).most_common(7)
top_words_wrong_predictions_as_not_propaganda

Most frequent words in sentences predicted as propaganda when not propaganda

In [ ]:
top_words_wrong_predictions_as_propaganda = Counter(" ".join(wrong_predictions_as_propaganda["sentence_"]).split()).most_common(7)
top_words_wrong_predictions_as_propaganda

##### Length of sentences

In [ ]:
lendf = results_df
lendf["accuracy_RF1"] =lendf["accuracy_RF1"].map({1:"Correct",0:"Incorrect"})
lendf["binary_label"] =lendf["binary_label"].map({1:"Propaganda",0:"Not_propaganda"})

#Histogram
alt.Chart(
    lendf,
    title = "Percentage of predictions per sentence length"
    ).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    y=alt.Y("sentence_length:O",
            title = "Number of words in sentence",
            bin = alt.Bin(step = 10),
            ),
    x = alt.X("sum(pct):Q",axis=alt.Axis(format='%'),
              title = "Number of predictions",
              stack  = "normalize"
              ),
    color = "accuracy_RF1:O"
)

alt.Chart(...)

In [ ]:
alt.Chart(lendf).mark_boxplot(ticks = True, size = 10).encode(
    y= alt.Y('accuracy_RF1:O', axis = None),
    x=alt.X('sentence_length:Q', title = "Numnber of words",),
    color = alt.Color("accuracy_RF1:N"),
    row = alt.Row("binary_label:N",align = "none",title = "", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.1,
).configure_header(
    labelOrient = "left",
    labelAlign = "left",
    labelAngle = 0,
)

alt.Chart(...)

##### Boundary predictions

In [ ]:
results_df[results_df["prob_prop_RF1"].between(0.46,0.54)]

Unnamed: 0.1  Unnamed: 0                      label  \
22             22          22      name_calling,labeling   
52             52          52                      doubt   
58             58          58             not_propaganda   
85             85          85            loaded_language   
88             88          88   appeal_to_fear_prejudice   
114           114         114            loaded_language   
123           123         123             not_propaganda   
125           125         125             not_propaganda   
160           160         160                      doubt   
229           229         229             not_propaganda   
230           230         230             not_propaganda   
243           243         243  exaggeration,minimisation   
245           245         245             not_propaganda   
257           257         257             not_propaganda   
268           268         268             not_propaganda   
273           273         273             not_propaganda   
278           278         278             not_propaganda   
286           286         286             not_propaganda   
292           292         292  causal_oversimplification   
297           297         297             not_propaganda   
315           315         315             not_propaganda   
323           323         323                flag_waving   
346           346         346             not_propaganda   
361           361         361             not_propaganda   
374           374         374             not_propaganda   
383           383         383      name_calling,labeling   
385           385         385      name_calling,labeling   
406           406         406      name_calling,labeling   
457           457         457             not_propaganda   
462           462         462                 repetition   
515           515         515             not_propaganda   
543           543         543             not_propaganda   
549           549         549             not_propaganda   
570           570         570            loaded_language   
585           585         585                 repetition   
593           593         593                      doubt   
596           596         596                flag_waving   
620           620         620             not_propaganda   
622           622         622                      doubt   
627           627         627             not_propaganda   
634           634         634             not_propaganda   
639           639         639  causal_oversimplification   

                                     tagged_in_context    binary_label  \
22   In Alexandra, Virginia – <BOS> the suburban ho...      Propaganda   
52   <BOS> Instead of reaching out to the greatest ...      Propaganda   
58   And he may do so even though the implications ...  Not_propaganda   
85   An outbreak of the plague in Madagascar is spr...      Propaganda   
88   And guess what, <BOS> next time a man is nomin...      Propaganda   
114  As for my metaphorical reference to a “Leviath...      Propaganda   
123  You don’t have to look far for fresh news abou...  Not_propaganda   
125  After Ford’s identity became public, Grassley’...  Not_propaganda   
160  Now that ISIS has been driven out of Raqqa and...      Propaganda   
229  Hence it is a time when they’re supposed to gr...  Not_propaganda   
230  Instead of establishing judgment within the ga...  Not_propaganda   
243  <BOS> Any purge would empty parishes and relig...      Propaganda   
245  The letter is not from the dubia cardinals, or...  Not_propaganda   
257  We have, actually, many <BOS> names,” he said....  Not_propaganda   
268  ICE arrests 20 in Kansas City during 4-day ope...  Not_propaganda   
273  3 black men (one with an Arabic/possibly Islam...  Not_propaganda   
278  An <BOS> old friend he had not seen in more th...  Not_propaganda   
286  The life insurance change’s timing seems to co...  Not_propaganda   
292  <BOS> The sta

## RoBERTa


In [ ]:
#Prepare datasets
train_dataset = traindf.drop(["label","span","tagged_in_context","span_length",	"sentence_length","type","len"], axis = 1)
train_dataset.rename(columns={"binary_label": "label","sentence":"text"}, inplace=True)

#Split training into validation and training
train_dataset, validation_dataset = train_test_split(train_dataset, test_size=0.2)
train_dataset = Dataset.from_pandas(train_dataset)
validation_dataset = Dataset.from_pandas(validation_dataset)


test_dataset = testdf.drop(["label","span","tagged_in_context","span_length",	"sentence_length","type","len"], axis = 1)
test_dataset.rename(columns={"binary_label": "label","sentence":"text"}, inplace=True)
test_dataset = Dataset.from_pandas(test_dataset)
train_dataset

Dataset({
    features: ['label', 'text', '__index_level_0__'],
    num_rows: 2046
})

### Sweep to choose hyperparameters using wandb

In [ ]:
sweep_config = {
    'method': 'random'
}


# hyperparameters
parameters_dict = {
    'epochs': {
        'value': 15
        },
    'learning_rate': {
        'distribution': 'uniform',
        'max': 0.0001,
        'min': 0.000016952978519689297
        },
    'weight_decay': {
        'values': [0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
        },

}


sweep_config['parameters'] = parameters_dict
sweep_id = wandb.sweep(sweep_config, project='nlp_propaganda')

def model_init():
  model = AutoModelForSequenceClassification.from_pretrained("roberta-base", num_labels=2)
  return model

def compute_metrics(eval_pred):
    accuracy = evaluate.load("accuracy")
    precision = evaluate.load("precision")
    recall = evaluate.load("recall")
    f1 = evaluate.load("f1")
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    accuracy = accuracy.compute(predictions = predictions, references = labels)
    precision = precision.compute(predictions = predictions, references = labels)
    recall = recall.compute(predictions = predictions, references = labels)
    f1 = f1.compute(predictions = predictions, references = labels)
    return {"accuracy": accuracy["accuracy"],
            "precision": precision["precision"],
            "recall": recall["recall"],
            "f1": f1["f1"]}


Create sweep with ID: ry4cruss
Sweep URL: https://wandb.ai/pdc/nlp_propaganda/sweeps/ry4cruss


In [ ]:
def train(config=None):
  with wandb.init(config=config):
    # set sweep configuration
    config = wandb.config


    # set training arguments
    training_args = TrainingArguments(
        output_dir='/content/drive/MyDrive/ANLP/models/task1',
	      report_to='wandb',  # Turn on Weights & Biases logging
        num_train_epochs=config.epochs,
        learning_rate=config.learning_rate,
        weight_decay=config.weight_decay,
        save_strategy='epoch',
        evaluation_strategy='epoch',
        logging_strategy='epoch',
        load_best_model_at_end=True,
        metric_for_best_model = "f1",
    )

    #define training loop
    trainer = Trainer(
        model= model_init(),
        args=training_args,
        train_dataset=tokenized_train_dataset,
        eval_dataset=tokenized_validation_dataset,
        compute_metrics=compute_metrics,
    )

    # start training loop
    trainer.train()


In [ ]:
wandb.agent(sweep_id, train, count=15)

wandb: Agent Starting Run: u64lqyy9 with config:
wandb: 	epochs: 15
wandb: 	learning_rate: 7.410297246846257e-05
wandb: 	weight_decay: 0.1


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

wandb: Agent Starting Run: ezkehlns with config:
wandb: 	epochs: 15
wandb: 	learning_rate: 4.597764598267162e-05
wandb: 	weight_decay: 0.4


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

wandb: Agent Starting Run: vov71ghj with config:
wandb: 	epochs: 15
wandb: 	learning_rate: 6.354964289508763e-05
wandb: 	weight_decay: 0.5


...

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: jd01chwx with config:
wandb: 	epochs: 15
wandb: 	learning_rate: 5.9193715985850456e-05
wandb: 	weight_decay: 0.4


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

wandb: Agent Starting Run: feo73s78 with config:
wandb: 	epochs: 15
wandb: 	learning_rate: 3.861271607392625e-05
wandb: 	weight_decay: 0.5


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifi

###  Final model

In [ ]:
#chose dataset
tokenizer = AutoTokenizer.from_pretrained("roberta-base")

def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)

#tokenize datasets
tokenized_train_dataset = train_dataset.map(tokenize_function, batched=True)
tokenized_validation_dataset = validation_dataset.map(tokenize_function, batched=True)
tokenized_test_dataset = test_dataset.map(tokenize_function, batched=True)


Map:   0%|          | 0/2046 [00:00<?, ? examples/s]

Map:   0%|          | 0/512 [00:00<?, ? examples/s]

Map:   0%|          | 0/640 [00:00<?, ? examples/s]

In [ ]:
#select model
model = AutoModelForSequenceClassification.from_pretrained("roberta-base", num_labels=2)

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'lm_head.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.bias', 'lm_head.layer_norm.bias', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

In [ ]:
#Select metrics for model evaluation

def compute_metrics(eval_pred):
    accuracy = evaluate.load("accuracy")
    precision = evaluate.load("precision")
    recall = evaluate.load("recall")
    f1 = evaluate.load("f1")
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    accuracy = accuracy.compute(predictions = predictions, references = labels)
    precision = precision.compute(predictions = predictions, references = labels)
    recall = recall.compute(predictions = predictions, references = labels)
    f1 = f1.compute(predictions = predictions, references = labels)
    return {"accuracy": accuracy["accuracy"],
            "precision": precision["precision"],
            "recall": recall["recall"],
            "f1": f1["f1"]}

In [ ]:
#Define arguments for training
training_args = TrainingArguments(output_dir="test_trainer",
                                  report_to = "wandb",
                                  save_strategy = "epoch",
                                  load_best_model_at_end = True,
                                  evaluation_strategy = "epoch",
                                  num_train_epochs = 7,
                                  weight_decay = 0.1,
                                  learning_rate = 0.00006355
                                  )

In [ ]:
#Initisialise trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_train_dataset,
    eval_dataset=tokenized_validation_dataset,
    compute_metrics=compute_metrics,
)

In [ ]:
#Train model
wandb.init(project = "nlp_propaganda")
trainer.train()


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


TrainOutput(global_step=1792, training_loss=0.5485167077609471, metrics={'train_runtime': 1518.0314, 'train_samples_per_second': 9.435, 'train_steps_per_second': 1.18, 'total_flos': 3768276534865920.0, 'train_loss': 0.5485167077609471, 'epoch': 7.0})

In [ ]:
#evaluate
labels_pred = trainer.predict(tokenized_test_dataset)

### Results

In [ ]:
#Predictions to dataframe
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results.csv", index_col = 0)
results_df["label"] = testdf["label"]
results_df["predictions_num_roB1"] = labels_pred[1]
results_df["predictions_roB1"] = labels_pred[0].argmax(-1)
results_df["accuracy_roB1"] = np.where(results_df["binary_label"] != results_df["predictions_roB1"], 0,1)


In [ ]:
#Dataframes to store wrong predictions
wrong_predictions = results_df[results_df["accuracy_roB1"] ==0]
wrong_predictions["sentence_"] = [s.translate(str.maketrans('', '', string.punctuation)) for s in wrong_predictions["sentence"].apply(lambda x: x.lower()).apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
wrong_predictions["sentence_"] =  [s.translate(str.maketrans("”"," ","")) for s in wrong_predictions["sentence_"]]
wrong_predictions["sentence_"] = [s.translate(str.maketrans("“"," ","")) for s in wrong_predictions["sentence_"] ]

#predicted as not propaganda when propaganda
wrong_predictions_as_not_propaganda = wrong_predictions[wrong_predictions["binary_label"] ==1]
#predicted as propaganda when not propaganda
wrong_predictions_as_propaganda = wrong_predictions[wrong_predictions["binary_label"] ==0 ]
#results_df["predictions_roB1"] = results_df["predictions_roB1"].map({1:"propaganda",0:"not_propaganda"})

right_predictions = results_df[results_df["accuracy_roB1"] ==1]


In [ ]:
#Save file
results_df.to_csv("/content/drive/MyDrive/ANLP/results.csv")

In [ ]:
#Predictions to dataframe
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results.csv",index_col=0)


In [ ]:
#Metrics
print(sklearn.metrics.classification_report(results_df["predictions_roB1"], results_df["binary_label"]))


              precision    recall  f1-score   support

           0       0.89      0.85      0.87       345
           1       0.83      0.87      0.85       295

    accuracy                           0.86       640
   macro avg       0.86      0.86      0.86       640
weighted avg       0.86      0.86      0.86       640



In [ ]:
prop_answers = results_df.groupby(["predictions_roB1","accuracy_roB1"])["tagged_in_context"].count()
prop_answers = prop_answers.reset_index(name="count")
prop_answers["accuracy_roB1"] = prop_answers["accuracy_roB1"].map({1:"Correct",0:"Incorrect"})
prop_answers["predictions_roB1"] = prop_answers["predictions_roB1"].map({1:"Propaganda",0:"Not Propaganda"})
alt.Chart(prop_answers,
    title= "Model predictions "
    ).mark_bar().encode(
    alt.Y("predictions_roB1",
          title = "Label predicted by model"
          ),
    alt.X("count",
          title="Percentage of answers(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color =alt.Color("accuracy_roB1:O", title = ""))

alt.Chart(...)

In [ ]:
right_answers =results_df.groupby(["binary_label","accuracy_roB1"])["tagged_in_context"].count()
right_answers = right_answers.reset_index(name ="count")

right_answers["accuracy_roB1"] = right_answers["accuracy_roB1"].map({1:"Correct",0:"Incorrect"})
right_answers["binary_label"] = right_answers["binary_label"].map({1:"Correct",0:"Incorrect"})

alt.Chart(right_answers,
    title= "Percentage of correct predictions per label"
    ).mark_bar().encode(
    y = alt.Y("binary_label:O",
          title = "True label"
          ),
    x = alt.X("count",
          title="Percentage of answers(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color = alt.Color("accuracy_roB1:O", title = "")
 )

alt.Chart(...)

In [ ]:
alt.Chart(
    wrong_predictions_as_not_propaganda,
    title= "Propaganda sentences labelled as Not propaganda"
    ).transform_joinaggregate(
    totalCount="count(*)"
    ).transform_calculate(
    PercentOfTotal="1 / datum.totalCount"
    ).mark_bar().encode(
    alt.Y("label",
          title = "True Label"),
    alt.X( "sum(PercentOfTotal):Q",
          title="Percentage of wrong answers(%)",
          axis=alt.Axis(format="%"),
          ),
    color =alt.Color("label", legend = None))



alt.Chart(...)

### length of sentence


In [ ]:
lendf = results_df
lendf["accuracy_roB1"] =lendf["accuracy_roB1"].map({1:"Correct",0:"Incorrect"})
lendf["binary_label"] =lendf["binary_label"].map({1:"Propaganda",0:"Not_propaganda"})

#Histogram
alt.Chart(
    lendf,
    title = "Percentage of predictions per sentence length"
    ).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    y=alt.Y("span_length:O",
            title = "Number of words in sentence",
            bin = alt.Bin(step = 5),

            ),
    x = alt.X("sum(pct):Q",axis=alt.Axis(format='%'),
              title = "Number of predictions",
               stack = "normalize"),
    color = "accuracy_roB1:O"
)

alt.Chart(...)

In [ ]:
alt.Chart(lendf).mark_boxplot(ticks = True, size = 10).encode(
    y= alt.Y('accuracy_roB1:O', axis = None),
    x=alt.X('sentence_length:Q', title = "Numnber of words",),
    color = alt.Color("accuracy_roB1:N"),
    row = alt.Row("binary_label:N",align = "none",title = "", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.1,
).configure_header(
    labelOrient = "left",
    labelAlign = "left",
    labelAngle = 0,
)

alt.Chart(...)

## Comparison

In [ ]:
both_wrong = results_df[(results_df.accuracy_RF1 == "Incorrect") & (results_df.accuracy_roB1 == "Incorrect")]
both_right = results_df[(results_df.accuracy_RF1 == "Correct") & (results_df.accuracy_roB1 == "Correct")]
rob_right = results_df[(results_df.accuracy_RF1 == "Incorrect") & (results_df.accuracy_roB1 == "Correct")]
rf_right = results_df[(results_df.accuracy_RF1 == "Correct") & (results_df.accuracy_roB1 == "Incorrect")]

In [ ]:
both_wrong

In [ ]:
both_right

In [ ]:
rob_right

In [ ]:
rf_right

# Task 2 -multiclass

## Baseline

In [ ]:
from sklearn.dummy import DummyClassifier


corpus_train = propaganda_train_df["span"]
labels_train = propaganda_train_df["label"].values

corpus_test = propaganda_test_df["span"]
labels_test = propaganda_test_df["label"].values

# Create a dummy classifier that predicts classes randomly
random_clf = DummyClassifier(strategy='uniform', random_state=42)

# Train the classifier on your training data
random_clf.fit(corpus_train, labels_train)

# Test the classifier on your test data
labels_pred = random_clf.predict(corpus_test)
print(sklearn.metrics.classification_report(labels_test, labels_pred))

                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.02      0.02      0.02        43
causal_oversimplification       0.11      0.11      0.11        35
                    doubt       0.14      0.12      0.13        43
exaggeration,minimisation       0.13      0.20      0.16        30
              flag_waving       0.14      0.11      0.12        45
          loaded_language       0.28      0.26      0.27        39
    name_calling,labeling       0.19      0.24      0.21        34
               repetition       0.17      0.15      0.16        40

                 accuracy                           0.15       309
                macro avg       0.15      0.15      0.15       309
             weighted avg       0.15      0.15      0.14       309



## Random Forest

#### Implementation

In [ ]:
corpus_train = [s.translate(str.maketrans('', '', string.punctuation)) for s in propaganda_train_df["span"].apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
corpus_train = [s.translate(str.maketrans("”"," ","")) for s in corpus_train]
corpus_train= [s.translate(str.maketrans("“"," ","")) for s in corpus_train]
labels_train = propaganda_train_df["label"].values
corpus_train_sub, corpus_validation, labels_train_sub, labels_validation = train_test_split(corpus_train, labels_train, test_size=0.2, random_state=1)

corpus_test = [s.translate(str.maketrans('', '', string.punctuation)) for s in propaganda_test_df["span"].apply(lambda x: x.lower()).apply(lambda x: ' '.join([word for word in x.split() if word not in (stopwords)]))]
corpus_test = [s.translate(str.maketrans("”"," ","")) for s in corpus_test]
corpus_test = [s.translate(str.maketrans("“"," ","")) for s in corpus_test]
labels_test = propaganda_test_df["label"].values


#### Function to perform a run with chosen parameters.


In [ ]:
def run_sweep(x_tr, y_tr, x_te, y_te,name, max_depth, n_estimators, n_gram_range,max_features):
  vectorizer = CountVectorizer(analyzer = "word", ngram_range=n_gram_range)
  x_train = vectorizer.fit_transform(x_tr)
  x_test = vectorizer.transform(x_te)
  feature_names = ["span"]

  test_size = 0.19372077488309952

  # train model
  model = RandomForestClassifier(n_estimators = n_estimators,
                                 random_state = 21,
                                 max_features=max_features,
                                 max_depth =max_depth,
                                 )
  model.fit(x_train, y_tr)
  labels =  model.classes_
  model_params = model.get_params()
  model_params["n_gram_range"]=n_gram_range[1]
  # get predictions
  labels_pred = model.predict(x_test)
  labels_probas = model.predict_proba(x_test)
  importances = model.feature_importances_
  indices = np.argsort(importances)[::-1]

  print(sklearn.metrics.classification_report(y_te, labels_pred))

  # start a new wandb run and add your model hyperparameters
  wandb.init(project='NLP_techniques', tags = ["keep"],config=model_params, name = name,settings=wandb.Settings(start_method="thread") )



  #log metrics to wandb
  accuracy = sklearn.metrics.accuracy_score(y_te, labels_pred)
  precision = sklearn.metrics.precision_score(y_te, labels_pred, average = "macro")
  recall = sklearn.metrics.recall_score(y_te, labels_pred, average = "macro")
  f1 = sklearn.metrics.f1_score(y_te, labels_pred, average = "macro")

  wandb.summary["accuracy"] = accuracy
  wandb.summary["f1"] = f1
  wandb.summary["precision"] = precision
  wandb.summary["recall"] = recall

  # [optional] finish the wandb run, necessary in notebooks
  wandb.finish()

In [ ]:
param_grid = {
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [3,5,7]
}

param_combinations = sorted(param_grid)
param_combinations = [item for item in it.product(*(param_grid[param] for param in param_grid))]


Run multiple parameter combinations

In [ ]:
#Unigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(x_tr= corpus_train_sub,
            y_tr = labels_train_sub,
            x_te = corpus_validation,
            y_te = labels_validation,
            name = "RFunigram"+str(n),
            n_estimators = param[0],
            n_gram_range = (1,1),
            max_features = param[1],
            max_depth = param[2],

  )
  n+=1

(200, 'auto', 3)


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.33      0.14      0.20        28
causal_oversimplification       0.64      0.17      0.27        40
                    doubt       0.52      0.45      0.48        29
exaggeration,minimisation       1.00      0.03      0.05        40
              flag_waving       0.71      0.50      0.59        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.14      0.93      0.25        28
               repetition       1.00      0.10      0.18        30

                 accuracy                           0.28       258
                macro avg       0.54      0.29      0.25       258
             weighted avg       0.57      0.28      0.25       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(200, 'auto', 5)


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.00      0.00      0.00        28
causal_oversimplification       0.33      0.03      0.05        40
                    doubt       0.33      0.03      0.06        29
exaggeration,minimisation       0.67      0.05      0.09        40
              flag_waving       1.00      0.03      0.06        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.11      1.00      0.21        28
               repetition       0.00      0.00      0.00        30

                 accuracy                           0.13       258
                macro avg       0.31      0.14      0.06       258
             weighted avg       0.34      0.13      0.06       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(500, 'log2', 5)
                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.42      0.18      0.25        28
causal_oversimplification       0.57      0.10      0.17        40
                    doubt       0.40      0.07      0.12        29
exaggeration,minimisation       0.30      0.07      0.12        40
              flag_waving       0.67      0.12      0.20        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.13      1.00      0.23        28
               repetition       0.67      0.07      0.12        30

                 accuracy                           0.19       258
                macro avg       0.39      0.20      0.15       258
             weighted avg       0.40      0.19      0.15       258



(500, 'log2', 7)
                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.45      0.18      0.26        28
causal_oversimplification       0.70      0.17      0.28        40
                    doubt       0.38      0.10      0.16        29
exaggeration,minimisation       0.42      0.12      0.19        40
              flag_waving       0.80      0.35      0.49        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.14      1.00      0.25        28
               repetition       0.50      0.07      0.12        30

                 accuracy                           0.24       258
                macro avg       0.42      0.25      0.22       258
             weighted avg       0.44      0.24      0.22       258



In [ ]:
#Bigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(
            x_tr= corpus_train_sub,
            y_tr = labels_train_sub,
            x_te = corpus_validation,
            y_te = labels_validation,
            name = "RFbigram"+str(n),
            n_estimators = param[0],
            n_gram_range = (1,2),
            max_features = param[1],
            max_depth = param[2],

            )
  n+=1

(200, 'auto', 3)


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.33      0.11      0.16        28
causal_oversimplification       0.50      0.03      0.05        40
                    doubt       0.40      0.14      0.21        29
exaggeration,minimisation       0.00      0.00      0.00        40
              flag_waving       0.74      0.50      0.60        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.12      0.93      0.22        28
               repetition       1.00      0.07      0.12        30

                 accuracy                           0.21       258
                macro avg       0.39      0.22      0.17       258
             weighted avg       0.39      0.21      0.16       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(200, 'auto', 5)


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.00      0.00      0.00        28
causal_oversimplification       0.50      0.03      0.05        40
                    doubt       0.00      0.00      0.00        29
exaggeration,minimisation       0.00      0.00      0.00        40
              flag_waving       1.00      0.03      0.06        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.11      1.00      0.20        28
               repetition       1.00      0.03      0.06        30

                 accuracy                           0.12       258
                macro avg       0.33      0.14      0.05       258
             weighted avg       0.34      0.12      0.04       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(500, 'log2', 5)
                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.00      0.00      0.00        28
causal_oversimplification       0.67      0.05      0.09        40
                    doubt       0.67      0.07      0.12        29
exaggeration,minimisation       0.00      0.00      0.00        40
              flag_waving       1.00      0.09      0.16        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.11      1.00      0.21        28
               repetition       1.00      0.03      0.06        30

                 accuracy                           0.14       258
                macro avg       0.43      0.16      0.08       258
             weighted avg       0.44      0.14      0.08       258



(500, 'log2', 7)
                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.33      0.04      0.06        28
causal_oversimplification       0.67      0.05      0.09        40
                    doubt       0.60      0.10      0.18        29
exaggeration,minimisation       0.00      0.00      0.00        40
              flag_waving       0.89      0.24      0.37        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.12      1.00      0.21        28
               repetition       1.00      0.07      0.12        30

                 accuracy                           0.17       258
                macro avg       0.45      0.19      0.13       258
             weighted avg       0.45      0.17      0.13       258



In [ ]:
#Trigram
param_combinations
n=0
for param in param_combinations:
  print(param)
  run_sweep(x_tr= corpus_train_sub,
            y_tr = labels_train_sub,
            x_te = corpus_validation,
            y_te = labels_validation,
            name = "RFtrigram"+str(n),
            n_estimators = param[0],
            n_gram_range = (1,3),
            max_features = param[1],
            max_depth = param[2],

            )
  n+=1

(200, 'auto', 3)


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.56      0.18      0.27        28
causal_oversimplification       1.00      0.05      0.10        40
                    doubt       0.60      0.21      0.31        29
exaggeration,minimisation       0.25      0.03      0.05        40
              flag_waving       0.81      0.38      0.52        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.13      1.00      0.23        28
               repetition       0.00      0.00      0.00        30

                 accuracy                           0.21       258
                macro avg       0.42      0.23      0.18       258
             weighted avg       0.44      0.21      0.18       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(200, 'auto', 5)


...

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(500, 'log2', 7)


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.00      0.00      0.00        28
causal_oversimplification       0.50      0.03      0.05        40
                    doubt       0.50      0.03      0.06        29
exaggeration,minimisation       0.00      0.00      0.00        40
              flag_waving       1.00      0.03      0.06        34
          loaded_language       0.00      0.00      0.00        29
    name_calling,labeling       0.11      1.00      0.20        28
               repetition       1.00      0.03      0.06        30

                 accuracy                           0.12       258
                macro avg       0.39      0.14      0.05       258
             weighted avg       0.39      0.12      0.05       258



/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


#### Final model

In [ ]:
vectorizer = CountVectorizer(analyzer = "word", ngram_range=(1,1))
x_train = vectorizer.fit_transform(corpus_train)
x_test = vectorizer.transform(corpus_test)
feature_names = ["sentence"]

test_size = 0.19372077488309952

# train model
model = RandomForestClassifier(n_estimators = 7,
                                 max_features="auto",
                                 max_depth =200)
model.fit(x_train, labels_train)
labels = model.classes_
model_params = model.get_params()
model_params["n_gram_range"]=2

# get predictions
labels_pred = model.predict(x_test)
labels_probas = model.predict_proba(x_test)
importances = model.feature_importances_
indices = np.argsort(importances)[::-1]
# start a new wandb run and add your model hyperparameters
wandb.init(project='NLP_RF1_', config=model_params, name = "Final")
# Add additional configs to wandb
wandb.config.update({"test_size" : test_size,
                    "train_len" : len(corpus_train),
                    "test_len" : len(corpus_test)})

# log additional visualisations to wandb
plot_class_proportions(labels_train, labels_test, labels)
plot_learning_curve(model, x_train, labels_train)
plot_roc(labels_test, labels_probas, labels)
plot_precision_recall(labels_test, labels_probas, labels)
plot_feature_importances(model)
wandb.sklearn.plot_classifier(model, x_train, x_test,labels_train, labels_test, labels_pred, labels_probas,labels ,
                                                        model_name="Final", feature_names=None)
print(sklearn.metrics.classification_report(labels_test, labels_pred))

#log metrics to wandb
accuracy = sklearn.metrics.accuracy_score(labels_test, labels_pred)
precision = sklearn.metrics.precision_score(labels_test, labels_pred, average ="macro")
recall = sklearn.metrics.recall_score(labels_test, labels_pred,average ="macro")
f1 = sklearn.metrics.f1_score(labels_test, labels_pred,average ="macro")

wandb.summary["accuracy"] = accuracy
wandb.summary["f1"] = f1
wandb.summary["precision"] = precision
wandb.summary["recall"] = recall

# [optional] finish the wandb run, necessary in notebooks
wandb.finish()

wandb: 
wandb: Plotting Final.
wandb: Logged feature importances.
wandb: Logged confusion matrix.
wandb: Logged summary metrics.
wandb: Logged class proportions.
wandb: WARNING This function only supports binary classification at the moment and therefore expects labels to be binary. Skipping calibration curve.
wandb: Logged calibration curve.
wandb: Logged roc curve.
wandb: Logged precision-recall curve.


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.45      0.23      0.31        43
causal_oversimplification       0.41      0.20      0.27        35
                    doubt       0.58      0.33      0.42        43
exaggeration,minimisation       0.27      0.37      0.31        30
              flag_waving       0.69      0.69      0.69        45
          loaded_language       0.29      0.85      0.43        39
    name_calling,labeling       0.50      0.32      0.39        34
               repetition       0.52      0.30      0.38        40

                 accuracy                           0.42       309
                macro avg       0.46      0.41      0.40       309
             weighted avg       0.48      0.42      0.41       309



In [ ]:
labels_pred =

#### Results

##### Save new result

In [ ]:
results_task2_df = propaganda_test_df
results_task2_df.to_csv("/content/drive/MyDrive/ANLP/results_task2.csv", index = 0)

In [ ]:
results_df.reset_index()

In [ ]:
#Predictions to dataframe
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results_task2.csv")
results_df["predictions_RF"] = labels_pred
results_df["accuracy_RF"] = np.where(results_df["label"] != results_df["predictions_RF"], "Incorrect","Correct")

wrong_predictions = results_df[results_df["accuracy_RF"] =="Incorrect"]

right_predictions = results_df[results_df["accuracy_RF"] =="Correct"]



In [ ]:
results_df.to_csv("/content/drive/MyDrive/ANLP/results_task2.csv")

#### Get old result

In [ ]:
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results_task2.csv", index_col = 0)

In [ ]:
print(sklearn.metrics.classification_report(results_df["label"],results_df["predictions_RF"]))

                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.45      0.23      0.31        43
causal_oversimplification       0.41      0.20      0.27        35
                    doubt       0.58      0.33      0.42        43
exaggeration,minimisation       0.27      0.37      0.31        30
              flag_waving       0.69      0.69      0.69        45
          loaded_language       0.29      0.85      0.43        39
    name_calling,labeling       0.50      0.32      0.39        34
               repetition       0.52      0.30      0.38        40

                 accuracy                           0.42       309
                macro avg       0.46      0.41      0.40       309
             weighted avg       0.48      0.42      0.41       309



#### Graphs classes

In [ ]:
prop_answers = results_df.groupby(["predictions_RF","accuracy_RF"]).count()
prop_answers = prop_answers.reset_index()

pred_acc = alt.Chart(prop_answers,
    title= "Precision"
    ).mark_bar().encode(
    alt.Y("predictions_RF",
          title = "Label predicted by model"
          ),
    alt.X("sum(tagged_in_context)",
          title="Percentage of predictions(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color =alt.Color("accuracy_RF:O", title = "Prediction"))
pred_acc

alt.Chart(...)

In [ ]:
right_answers =results_df.groupby(["label","accuracy_RF"])["tagged_in_context"].count()
right_answers = right_answers.reset_index(name ="count")

label_acc = alt.Chart(right_answers,
    title= "Recall"
    ).mark_bar().encode(
    alt.Y("label",
          title = "True label"
          ),
    alt.X("count",
          title="Percentage of sentences(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    alt.Color("accuracy_RF:O", title = "Prediction", )
 )
label_acc


alt.Chart(...)

#### Length of wrong sentences

In [ ]:
len_df = results_df

In [ ]:
#Histogram
alt.Chart(
    len_df,
    title = "Percentage of predictions per span length"
    ).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    y=alt.Y("span_length:O",
            title = "Number of words in span",
            bin = alt.Bin(step = 10),
            ),
    x = alt.X("sum(pct):Q",axis=alt.Axis(format='%'),
              title = "Percentage of spans",
               stack = "normalize"),
    color = alt.Color("accuracy_RF:O", title = "Prediction")
)

alt.Chart(...)

In [ ]:
alt.Chart(len_df).mark_boxplot(ticks = True, size = 10).encode(
    x= alt.X('accuracy_RF:O', axis = None, title = "Prediction"),
    y=alt.Y('span_length:Q', title = "Numnber of words",),
    color = alt.Color("accuracy_RF:N", title = "Prediction"),
    column = alt.Column("label:N",align = "none",title = "True label", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.2,
).configure_header(
    labelOrient = "bottom",
    labelAlign = "right",
    labelAngle = -90,
    titleOrient = "bottom"
)

alt.Chart(...)

Examples of predictions

#### Boundary predictions

In [ ]:
results_df[results_df["prob_prop_RF2"].between(0.46,0.54)]

## RoBERTa

### Default


In [ ]:
#Prepare datasets
train_dataset = propaganda_train_df.drop(["binary_label","sentence","tagged_in_context","span_length",	"sentence_length","type","len"], axis = 1)
train_dataset['label'] = train_dataset.label.astype('category')
train_dataset['label'] = train_dataset['label'].cat.codes
train_dataset.rename(columns={"span":"text"}, inplace=True)

#Split training into validation and training
train_dataset, validation_dataset = train_test_split(train_dataset, test_size=0.2, stratify = train_dataset["label"])
print(validation_dataset.groupby("label").count())

print(train_dataset.groupby("label").count())
train_dataset = train_dataset.reset_index(drop=True)
train_dataset = Dataset.from_pandas(train_dataset)


validation_dataset = validation_dataset.reset_index(drop=True)
validation_dataset = Dataset.from_pandas(validation_dataset)


test_dataset = propaganda_test_df.drop(["binary_label","sentence","tagged_in_context","span_length",	"sentence_length","type","len"], axis = 1)
test_dataset['label'] = test_dataset.label.astype('category')
test_dataset['label'] = test_dataset['label'].cat.codes
test_dataset.rename(columns={"span":"text"}, inplace=True)
test_dataset = test_dataset.reset_index(drop=True)
test_dataset = Dataset.from_pandas(test_dataset)


In [ ]:
#chose tokenizer
tokenizer = AutoTokenizer.from_pretrained("roberta-base")

def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)

#tokenize datasets
tokenized_train_dataset = train_dataset.map(tokenize_function, batched=True)
tokenized_validation_dataset = validation_dataset.map(tokenize_function, batched=True)
tokenized_test_dataset = test_dataset.map(tokenize_function, batched=True)


Map:   0%|          | 0/1032 [00:00<?, ? examples/s]

Map:   0%|          | 0/258 [00:00<?, ? examples/s]

Map:   0%|          | 0/309 [00:00<?, ? examples/s]

In [ ]:
#select model
model = AutoModelForSequenceClassification.from_pretrained("roberta-base", num_labels=8)

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

In [ ]:
def model_init():
  model = AutoModelForSequenceClassification.from_pretrained("roberta-base", num_labels=8)
  return model

def compute_metrics(eval_pred):
    accuracy = evaluate.load("accuracy")
    precision = evaluate.load("precision")
    recall = evaluate.load("recall")
    f1 = evaluate.load("f1")
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    accuracy = accuracy.compute(predictions = predictions, references = labels)
    precision = precision.compute(predictions = predictions, references = labels, average="macro")
    recall = recall.compute(predictions = predictions, references = labels, average="macro")
    f1 = f1.compute(predictions = predictions, references = labels, average="macro")
    return {"accuracy": accuracy["accuracy"],
            "precision": precision["precision"],
            "recall": recall["recall"],
            "f1": f1["f1"]}


### sweep w&b

In [ ]:
sweep_config = {
    'method': 'random'
}

# hyperparameters
parameters_dict = {
    'epochs': {
        'distribution': 'int_uniform',
        'max': 25,
        'min': 10
        },
    'learning_rate': {
        'distribution': 'uniform',
        'max': 0.0001,
        'min': 0.000016952978519689297
        },
    'weight_decay': {
        'values': [0.0, 0.1, 0.2  , 0.3, 0.4, 0.5]
        },
    "train_batch_size": {
      "distribution": "int_uniform",
      "max": 16,
      "min": 4
      }
}


sweep_config['parameters'] = parameters_dict
sweep_id = wandb.sweep(sweep_config, project='NLP_tecniques_roberta')



Create sweep with ID: 1fchmwd0
Sweep URL: https://wandb.ai/pdc/NLP_tecniques_roberta/sweeps/1fchmwd0


In [ ]:
def train(config=None):
  with wandb.init(config=config):
    # set sweep configuration
    config = wandb.config


    # set training arguments
    training_args = TrainingArguments(
        output_dir='/content/drive/MyDrive/ANLP/models/task2',
	      report_to='wandb',  # Turn on Weights & Biases logging
        num_train_epochs=config.epochs,
        learning_rate=config.learning_rate,
        weight_decay=config.weight_decay,
        save_total_limit = 2,
        save_strategy = "no",
        load_best_model_at_end=False,
        logging_strategy='epoch',
        metric_for_best_model = "f1",
        per_device_train_batch_size = config.train_batch_size,
        evaluation_strategy="epoch"
    )

    #define training loop
    trainer = Trainer(
        model= model_init(),
        args=training_args,
        train_dataset=tokenized_train_dataset,
        eval_dataset=tokenized_validation_dataset,
        compute_metrics=compute_metrics,
    )
    # start training loop
    trainer.train()


In [ ]:
wandb.agent(sweep_id, train, count=15)

wandb: WARNING Calling wandb.login() after wandb.init() has no effect.
wandb: Agent Starting Run: accodx20 with config:
wandb: 	epochs: 21
wandb: 	learning_rate: 8.707693824609009e-05
wandb: 	train_batch_size: 9
wandb: 	weight_decay: 0.4


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning

wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: mqia1sa6 with config:
wandb: 	epochs: 10
wandb: 	learning_rate: 5.455396823725867e-05
wandb: 	train_batch_size: 4
wandb: 	weight_decay: 0.5


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

...

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

wandb: Agent Starting Run: 2cftuedj with config:
wandb: 	epochs: 12
wandb: 	learning_rate: 6.846828291307634e-05
wandb: 	train_batch_size: 11
wandb: 	weight_decay: 0.4


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.bias', 'lm_head.dense.weight', 'roberta.pooler.dense.bias', 'lm_head.decoder.weight', 'roberta.pooler.dense.weight', 'lm_head.dense.bias', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.bias', 'classifier.

Error in callback <function _WandbInit._pause_backend at 0x7f07c51c0e50> (for post_run_cell):


BrokenPipeError: ignored

### Final model


#### Training

In [ ]:
training_args = TrainingArguments(
    output_dir='/content/drive/MyDrive/ANLP/models/task2',
    report_to='wandb',  # Turn on Weights & Biases logging
    num_train_epochs=12,
    learning_rate=0.00004476,
    weight_decay=0.5,
    save_total_limit = 2,
    save_strategy = "epoch",
    load_best_model_at_end=True,
    logging_strategy='epoch',
    metric_for_best_model = "f1",
    per_device_train_batch_size = 4,
    evaluation_strategy="epoch"
)

#define training loop
trainer = Trainer(
    model= model_init(),
    args=training_args,
    train_dataset=tokenized_train_dataset,
    eval_dataset=tokenized_validation_dataset,
    compute_metrics=compute_metrics,
)
# start training loop
trainer.train()

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.weight', 'lm_head.decoder.weight', 'roberta.pooler.dense.bias', 'lm_head.bias', 'lm_head.layer_norm.bias', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.dense.weight', 'classifie

/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [ ]:
labels_pred = trainer.predict(tokenized_test_dataset)

#### Loading pre-trained model

### Results

In [ ]:
codes  = dict(enumerate(propaganda_train_df['label'].astype('category').cat.categories))

In [ ]:
#Predictions to dataframe
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results_task2.csv")
results_df["preidctions_num_roberta"] = labels_pred[0].argmax(-1)
results_df["predictions_roberta"] = results_df["preidctions_num_roberta"].map(codes)
results_df["accuracy_roberta"] = np.where(results_df["label"] != results_df["predictions_roberta"], "Incorrect","Correct")

wrong_predictions = results_df[results_df["accuracy_roberta"] =="Incorrect"]

right_predictions = results_df[results_df["accuracy_roberta"] =="Correct"]



In [ ]:
#Save file
results_df.to_csv("/content/drive/MyDrive/ANLP/results_task2.csv")

In [ ]:
#Predictions to dataframe
results_df = pd.read_csv("/content/drive/MyDrive/ANLP/results_task2.csv",index_col=0)


In [ ]:
print(sklearn.metrics.classification_report(results_df["predictions_roberta"], results_df["label"]))


                           precision    recall  f1-score   support

 appeal_to_fear_prejudice       0.70      0.68      0.69        44
causal_oversimplification       0.69      0.67      0.68        36
                    doubt       0.65      0.76      0.70        37
exaggeration,minimisation       0.73      0.56      0.64        39
              flag_waving       0.80      0.73      0.77        49
          loaded_language       0.46      0.58      0.51        31
    name_calling,labeling       0.71      0.71      0.71        34
               repetition       0.53      0.54      0.53        39

                 accuracy                           0.66       309
                macro avg       0.66      0.65      0.65       309
             weighted avg       0.67      0.66      0.66       309



In [ ]:
results_df[results_df["accuracy_roberta"]==0]

In [ ]:
codes  = dict(enumerate(traindf['label'].astype('category').cat.categories))


#### Classes

In [ ]:
prop_answers = results_df.groupby(["predictions_roberta","accuracy_roberta"]).count()
prop_answers = prop_answers.reset_index()


In [ ]:
alt.Chart(prop_answers,
    title= "Recall "
    ).mark_bar().encode(
    alt.Y("predictions_roberta",
          title = "True label"
          ),
    alt.X("tagged_in_context",
          title="Percentage of sentences(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    color =alt.Color("accuracy_roberta:O", title = "Predictions"))

alt.Chart(...)

In [ ]:
prop_answers = results_df.groupby(["label","accuracy_roberta"])["tagged_in_context"].count()
prop_answers = prop_answers.reset_index(name = "count")

In [ ]:
alt.Chart(prop_answers,
    title= "Precision"
    ).mark_bar().encode(
    alt.Y("label:O",
          title = "Prediction"
          ),
    alt.X("count",
          title="Percentage of predictions(%)",
          stack = "normalize",
          axis=alt.Axis(format='%')
          ),
    alt.Color("accuracy_roberta:O", title = "Prediction")

 )


alt.Chart(...)

#### Length

In [ ]:
#Histogram
alt.Chart(
    results_df,
    title = "Percentage of predictions per span length"
    ).transform_joinaggregate(
    total='count(*)'
).transform_calculate(
    pct='1 / datum.total'
).mark_bar().encode(
    y=alt.Y("span_length:O",
            title = "Number of words in span",
            bin = alt.Bin(step = 10),
           ),
    x = alt.X("sum(pct):Q",axis=alt.Axis(format='%'),
              title = "Number of spans",
               stack = "normalize"),
    color = "accuracy_roberta:O"
)

alt.Chart(...)

In [ ]:
alt.Chart(results_df).mark_boxplot(ticks = True, size = 10).encode(
    y= alt.Y('label:O', axis = None),
    x=alt.X('span_length:Q', title = "Number of words",),
    color = alt.Color("accuracy_roberta:N", title = "Prediction"),
    row = alt.Row("binary_label:N",align = "none",title = "", spacing = 0.2)
).configure_view(
    stroke="transparent"
).configure_scale(
    bandPaddingInner=0,
    bandPaddingOuter=0.1,
).configure_header(
    labelOrient = "left",
    labelAlign = "left",
    labelAngle = 0,
)

## Comparison




In [ ]:
both_wrong = results_df[(results_df.accuracy_RF == "Incorrect") & (results_df.accuracy_roberta == "Incorrect")]
both_right = results_df[(results_df.accuracy_RF == "Correct") & (results_df.accuracy_roberta == "Correct")]
rob_right = results_df[(results_df.accuracy_RF == "Incorrect") & (results_df.accuracy_roberta == "Correct")]
rf_right = results_df[(results_df.accuracy_RF == "Correct") & (results_df.accuracy_roberta == "Incorrect")]

In [ ]:
both_wrong.groupby("label")["tagged_in_context"].count()
both_wrong = both_wrong.groupby("label")["tagged_in_context"].count().reset_index(name = "count")
comparison_df =

Unnamed: 0  tagged_in_context  binary_label  \
label                                                                    
appeal_to_fear_prejudice            4                  4             4   
doubt                               2                  2             2   
exaggeration,minimisation           7                  7             7   
flag_waving                         1                  1             1   
loaded_language                     6                  6             6   
name_calling,labeling               9                  9             9   
not_propaganda                      3                  3             3   
repetition                          4                  4             4   

                           sentence  span  span_length  len  sentence_length  \
label                                                                          
appeal_to_fear_prejudice          4     4            4    4                4   
doubt                             2     2            2    2                2   
exaggeration,minimisation         7     7            7    7                7   
flag_waving                       1     1            1    1                1   
loaded_language                   6     6            6    6                6   
name_calling,labeling             9     9            9    9                9   
not_propaganda                    3     3            3    3                3   
repetition                        4     4            4    4                4   

                           type  prob_prop_RF1  ...  RF1_accuracy  \
label                                           ...                 
appeal_to_fear_prejudice      4              4  ...             4   
doubt                         2              2  ...             2   
exaggeration,minimisation     7              7  ...             7   
flag_waving                   1              1  ...             1   
loaded_language               6              6  ...             6   
name_calling,labeling         9              9  ...             9   
not_propaganda                3              3  ...             3   
repetition                    4              4  ...             4   

                           prob_prop_RF2  predictions_RF2  accuracy_RF2  \
label                                                                     
appeal_to_fear_prejudice               4                4             4   
doubt                                  2                2             2   
exaggeration,minimisation              7                7             7   
flag_waving                            1                1             1   
loaded_language                        6                6             6   
name_calling,labeling                  9                9             9   
not_propaganda                         3                3             3   
repetition                             4                4             4   

                           predictions_roB2  accuracy_roB2  \
label                                                        
appeal_to_fear_prejudice                  4              4   
doubt                                     2              2   
exaggeration,minimisation                 7              7   
flag_waving                               1              1   
loaded_language                           6              6   
name_calling,labeling                     9              9   
not_propaganda                            3              3   
repetition                                4              4   

                           predictions_num_roB2  predictions_num_roB1  \
label                                                                   
appeal_to_fear_prejudice                      4                     4   
doubt                                         2                     2   
exaggeration,minimisation                     7                     7   
flag_waving                                   1          

In [ ]:
both_right.groupby("label").count()

Unnamed: 0  tagged_in_context  binary_label  sentence  span  \
label                                                                         
not_propaganda          15                 15            15        15    15   

                span_length  len  sentence_length  type  prob_prop_RF1  ...  \
label                                                                   ...   
not_propaganda           15   15               15    15             15  ...   

                RF1_accuracy  prob_prop_RF2  predictions_RF2  accuracy_RF2  \
label                                                                        
not_propaganda            15             15               15            15   

                predictions_roB2  accuracy_roB2  predictions_num_roB2  \
label                                                                   
not_propaganda                15             15                    15   

                predictions_num_roB1  predictions_roB1  accuracy_roB1  
label                                                                  
not_propaganda                    15                15             15  

[1 rows x 21 columns]

In [ ]:
rob_right.groupby("label").count()

Unnamed: 0  tagged_in_context  binary_label  \
label                                                                    
doubt                               5                  5             5   
exaggeration,minimisation           3                  3             3   
flag_waving                         1                  1             1   
loaded_language                     1                  1             1   
name_calling,labeling               2                  2             2   
not_propaganda                      7                  7             7   
repetition                          5                  5             5   

                           sentence  span  span_length  len  sentence_length  \
label                                                                          
doubt                             5     5            5    5                5   
exaggeration,minimisation         3     3            3    3                3   
flag_waving                       1     1            1    1                1   
loaded_language                   1     1            1    1                1   
name_calling,labeling             2     2            2    2                2   
not_propaganda                    7     7            7    7                7   
repetition                        5     5            5    5                5   

                           type  prob_prop_RF1  ...  RF1_accuracy  \
label                                           ...                 
doubt                         5              5  ...             5   
exaggeration,minimisation     3              3  ...             3   
flag_waving                   1              1  ...             1   
loaded_language               1              1  ...             1   
name_calling,labeling         2              2  ...             2   
not_propaganda                7              7  ...             7   
repetition                    5              5  ...             5   

                           prob_prop_RF2  predictions_RF2  accuracy_RF2  \
label                                                                     
doubt                                  5                5             5   
exaggeration,minimisation              3                3             3   
flag_waving                            1                1             1   
loaded_language                        1                1             1   
name_calling,labeling                  2                2             2   
not_propaganda                         7                7             7   
repetition                             5                5             5   

                           predictions_roB2  accuracy_roB2  \
label                                                        
doubt                                     5              5   
exaggeration,minimisation                 3              3   
flag_waving                               1              1   
loaded_language                           1              1   
name_calling,labeling                     2              2   
not_propaganda                            7              7   
repetition                                5              5   

                           predictions_num_roB2  predictions_num_roB1  \
label                                                                   
doubt                                         5                     5   
exaggeration,minimisation                     3                     3   
flag_waving                                   1                     1   
loaded_language                               1                     1   
name_calling,labeling                         2                     2   
not_propaganda                                7                     7   
repetition                                    5                     5   

                           predictions_roB1  accuracy_roB1  
label                                                       
do

In [ ]:
rf_right

Unnamed: 0           label  \
17           17  not_propaganda   
30           30  not_propaganda   
132         132  not_propaganda   
211         211  not_propaganda   
229         229  not_propaganda   
268         268  not_propaganda   
281         281  not_propaganda   
291         291  not_propaganda   
431         431  not_propaganda   
442         442           doubt   
444         444  not_propaganda   
523         523  not_propaganda   
534         534  not_propaganda   

                                     tagged_in_context  binary_label  \
17   @drawandstrike theory looking plausiblehttps:/...             0   
30   Rare but deadly, the viral disease is most com...             0   
132  At least, Israel has a more sympathetic ear in...             0   
211  And I don’t want to go <BOS> around insulting ...             0   
229  Hence it is a time when they’re supposed to gr...             0   
268  ICE arrests 20 in Kansas City during 4-day ope...             0   
281  I sold him 120 rounds of .556 tracer, again, s...             0   
291  To <BOS> achieve that and hold onto power the ...             0   
431  The meeting covered <BOS> Carmels of <EOS> the...             0   
442  As noted above, at this point literally every ...             1   
444  There already was a blackout on the worst mass...             0   
523  Strange ‘Sonic <BOS> Attacks’ Against Diplomat...             0   
534  After all, after the Trump White House issued ...             0   

                                              sentence  \
17   @drawandstrike theory looking plausiblehttps:/...   
30   Rare but deadly, the viral disease is most com...   
132  At least, Israel has a more sympathetic ear in...   
211  And I don’t want to go around insulting people.     
229  Hence it is a time when they’re supposed to gr...   
268  ICE arrests 20 in Kansas City during 4-day ope...   
281  I sold him 120 rounds of .556 tracer, again, s...   
291  To achieve that and hold onto power the prime ...   
431  The meeting covered Carmels of  the Teresian, ...   
442  As noted above, at this point literally every ...   
444  There already was a blackout on the worst mass...   
523  Strange ‘Sonic Attacks’ Against Diplomats  Rea...   
534  After all, after the Trump White House issued ...   

                                                  span  span_length  len  \
17                                                   —            1   78   
30                                             humans.            1   84   
132                                  to U.S. interests            3  234   
211                           around insulting people.            3   49   
229              and kind toward their fellow Muslims.            6  102   
268                                    criminal aliens            2   80   
281                                         military,"            1   90   
291  achieve that and hold onto power the prime min...           28  178   
431                                         Carmels of            2  207   
442  cannot be trusted and should be considered as ...            9  231   
444                                           history.            1   83   
523                         Attacks’ Against Diplomats            3   66   
534      why the statement was unsatisfactory to them.            7  199   

     sentence_length  type  ...  RF1_accuracy prob_prop_RF2  predictions_RF2  \
17                 8  Test  ...             0      0.000000   not_propaganda   
30                13  Test  ...             0      0.000000   not_propaganda   
132               40  Test  ...             0      0.000000   not_propaganda   
211                9  Test  ...             0      0.000000   not_propaganda   
229               18  Test  ...             0      0.000000   not_propaganda   
268               12  Test  ...             0      0.000000   not_propaganda   
281               16  Test  ...             0      0.000000   not_p